## Libraries

In [30]:
# !pip install geopy
import requests
from geopy.geocoders import Nominatim
import pandas as pd
import requests
import time

## Function for dropping the instances with NaN values

In [12]:
def drop_na_values(df):
    df.dropna(subset=['Latitude', 'Longitude'], inplace=True)
    df.dropna(subset=['Self-defined ethnicity'], inplace=True)
    df.dropna(subset=['Age range'], inplace=True)
    df.dropna(subset=['Gender'], inplace=True)
    df.dropna(subset=['Object of search'], inplace=True)
    df.dropna(subset=['Officer-defined ethnicity'], inplace=True)

## Function for convering the coordinates into London Boroughs

In this function Geocoding API of geopy is used to get the postcodes of the latitude anf longitude. Also, the Postcode & Geolocation API for the UK of postcodes.io is used in order to get the London boroughs from the postcodes produced.

In [14]:
def request_with_rate_limit(url, params=None, username=None, password=None):
    auth = (username, password) if username and password else None
    response = requests.get(url, params=params, auth=auth)
    if response.status_code == 429:
        seconds_to_wait = int(response.headers["Retry-After"])
        time.sleep(seconds_to_wait)
        return request_with_rate_limit(url, params=params, auth=auth)
    return response

counter = 0
def get_location(row):
    global counter
    counter += 1
    print(counter)
    lat = row["Latitude"]
    lng = row["Longitude"]

    try:
        nominatim_url = "https://nominatim.openstreetmap.org/reverse"
        nominatim_params = {"lat": lat, "lon": lng, "format": "json"}
        response = request_with_rate_limit(nominatim_url, params=nominatim_params)
        response.raise_for_status()
        location = response.json()
        if 'postcode' in location['address']:
            postcode = location['address']['postcode']
        else:
            return "No postal code found"
        if postcode:
            url = f"https://api.postcodes.io/postcodes/{postcode}"
            try:
                response = requests.get(url, timeout=10)
                response.raise_for_status()
                data = response.json()
                if data.get('result', {}).get('admin_district'):
                    borough = data['result']['admin_district']
                else:
                    borough = None
                print(borough)
                return borough
            except (requests.exceptions.RequestException, KeyError):
                pass
        return None
    except (requests.exceptions.RequestException, KeyError):
        return None

## Creating a list of all the dataframes

In [15]:
# Create a list of all the individual DataFrames
dfs = [pd.read_csv(f"../Data/Police_Data/Stop_And_Search/2020-{month:02}/2020-{month:02}-metropolitan-stop-and-search.csv") for month in range(1, 13)]

## EDA NULL VALUES

In [16]:
def null_values(dfs):
    concat_for_eda = pd.concat(dfs, ignore_index=True)
    concat_for_eda
    print("Number of instances: ", len(concat_for_eda))
    print(concat_for_eda.isnull().sum())

null_values(dfs)

Number of instances:  317505
Type                                             0
Date                                             0
Part of a policing operation                     0
Policing operation                          317505
Latitude                                     34340
Longitude                                    34340
Gender                                        4552
Age range                                    38391
Self-defined ethnicity                        4516
Officer-defined ethnicity                     7044
Legislation                                      0
Object of search                               707
Outcome                                          0
Outcome linked to object of search          317505
Removal of more than just outer clothing    317505
dtype: int64


## Dropping the NaN values for every dataframe in the list

In [22]:
for x in range(12):
    drop_na_values(dfs[x])

In [23]:
null_values(dfs)

Number of instances:  246737
Type                                             0
Date                                             0
Part of a policing operation                     0
Policing operation                          246737
Latitude                                         0
Longitude                                        0
Gender                                           0
Age range                                        0
Self-defined ethnicity                           0
Officer-defined ethnicity                        0
Legislation                                      0
Object of search                                 0
Outcome                                          0
Outcome linked to object of search          246737
Removal of more than just outer clothing    246737
dtype: int64


In [24]:
dfs[0]

Type                       Date  \
0                  Person search  2020-01-01T00:00:00+00:00   
1                  Person search  2020-01-01T00:01:00+00:00   
5      Person and Vehicle search  2020-01-01T00:10:00+00:00   
6                  Person search  2020-01-01T00:10:00+00:00   
7                  Person search  2020-01-01T00:15:00+00:00   
...                          ...                        ...   
28705              Person search  2020-01-31T23:45:00+00:00   
28706              Person search  2020-01-31T23:45:00+00:00   
28707              Person search  2020-01-31T23:45:00+00:00   
28709              Person search  2020-01-31T23:55:00+00:00   
28710              Person search  2020-01-31T23:57:00+00:00   

       Part of a policing operation  Policing operation   Latitude  Longitude  \
0                             False                 NaN  51.546371  -0.076007   
1                             False                 NaN  51.509232  -0.117576   
5                             False                 NaN  51.544707  -0.144062   
6                             False                 NaN  51.544707  -0.144062   
7                             False                 NaN  51.493239  -0.127411   
...                             ...                 ...        ...        ...   
28705                         False                 NaN  51.378427  -0.102657   
28706                         False                 NaN  51.377747  -0.099510   
28707                         False                 NaN  51.377747  -0.099510   
28709                         False                 NaN  51.500359  -0.277466   
28710                         False                 NaN  51.374945  -0.101422   

       Gender Age range                             Self-defined ethnicity  \
0        Male     25-34  Mixed/Multiple ethnic groups - Any other Mixed...   
1        Male     18-24  Black/African/Caribbean/Black British - Any ot...   
5        Male     25-34                    Other ethnic group - Not stated   
6        Male     25-34    Black/African/Caribbean/Black British - African   
7        Male     18-24                      Asian/Asian British - Chinese   
...       ...       ...                                                ...   
28705    Male     25-34                    Other ethnic group - Not stated   
28706  Female     18-24  White - English/Welsh/Scottish/Northern Irish/...   
28707    Male     10-17    Black/African/Caribbean/Black British - African   
28709    Male     18-24                      Asian/Asian British - Chinese   
28710    Male     18-24    Black/African/Caribbean/Black British - African   

      Officer-defined ethnicity  \
0                         Black   
1                         Black   
5                         Black   
6                         Black   
7                         Asian   
...                         ...   
28705                     Black   
28706                     White   
28707                     Black   
28709                     White   
28710                     Black   

                                             Legislation  \
0                  Misuse of Drugs Act 1971 (section 23)   
1      Police and Criminal Evidence Act 1984 (section 1)   
5                  Misuse of Drugs Act 1971 (section 23)   
6                  Misuse of Drugs Act 1971 (section 23)   
7      Police and Criminal Evidence Act 1984 (section 1)   
...                                                  ...   
28705  Criminal Justice and Public Order Act 1994 (se...   
28706              Misuse of Drugs Act 1971 (section 23)   
28707              Misuse of Drugs Act 1971 (section 23)   
28709  Police and Criminal Evidence Act 1984 (section 1)   
28710  Criminal Justice and Public Order Act 1994 (se...   

                          Object of search                       Outcome  \
0                         Controlled drugs  A no further action disposal   
1                                Fireworks                        A

## Categorising the Ethinicty

In [25]:
def ethnicity_catecories(sentence):
    words = str(sentence).split()
    first_word = words[0]
    if '/' in first_word:
        first_word = first_word.split('/')[0]

    return first_word

In [26]:
for x in range(12):
    dfs[x]['Self-defined ethnicity'] =  dfs[x]['Self-defined ethnicity'].apply(ethnicity_catecories)

In [27]:
dfs[1]

Type                       Date  \
0                  Person search  2020-02-01T00:00:00+00:00   
1                  Person search  2020-02-01T00:00:00+00:00   
2                  Person search  2020-02-01T00:02:00+00:00   
3                  Person search  2020-02-01T00:05:00+00:00   
4                  Person search  2020-02-01T00:05:00+00:00   
...                          ...                        ...   
23437  Person and Vehicle search  2020-02-29T23:51:00+00:00   
23438              Person search  2020-02-29T23:55:00+00:00   
23439              Person search  2020-02-29T23:55:00+00:00   
23442              Person search  2020-02-29T23:56:00+00:00   
23443  Person and Vehicle search  2020-02-29T23:58:00+00:00   

       Part of a policing operation  Policing operation   Latitude  Longitude  \
0                             False                 NaN  51.512098  -0.139407   
1                             False                 NaN  51.378427  -0.102657   
2                             False                 NaN  51.378427  -0.102657   
3                             False                 NaN  51.426626  -0.338871   
4                             False                 NaN  51.496767  -0.096321   
...                             ...                 ...        ...        ...   
23437                         False                 NaN  51.565103  -0.036417   
23438                         False                 NaN  51.523977  -0.075841   
23439                         False                 NaN  51.516120  -0.129961   
23442                         False                 NaN  51.539681  -0.142998   
23443                         False                 NaN  51.617805  -0.019626   

      Gender Age range Self-defined ethnicity Officer-defined ethnicity  \
0       Male     18-24                  Black                     Black   
1       Male     18-24                  White                     White   
2       Male   over 34                  Asian                     Asian   
3       Male     10-17                  White                     White   
4       Male     18-24                  Asian                     White   
...      ...       ...                    ...                       ...   
23437   Male     18-24                  Asian                     Asian   
23438   Male     25-34                  Black                     Black   
23439   Male     18-24                  Asian                     Asian   
23442   Male     18-24                  Other                     Black   
23443   Male     18-24                  Black                     Black   

                                             Legislation  \
0      Police and Criminal Evidence Act 1984 (section 1)   
1      Criminal Justice and Public Order Act 1994 (se...   
2      Criminal Justice and Public Order Act 1994 (se...   
3      Police and Criminal Evidence Act 1984 (section 1)   
4                  Misuse of Drugs Act 1971 (section 23)   
...                                                  ...   
23437              Misuse of Drugs Act 1971 (section 23)   
23438                     Firearms Act 1968 (section 47)   
23439  Police and Criminal Evidence Act 1984 (section 1)   
23442              Misuse of Drugs Act 1971 (section 23)   
23443              Misuse of Drugs Act 1971 (section 23)   

                          Object of search                       Outcome  \
0                             Stolen goods  A no further action disposal   
1      Anything to threaten or harm anyone  A no further action disposal   
2      Anything to threaten or harm anyone  A no further action disposal   
3                             Stolen goods   Penalty Notice for Disorder   
4                         Controlled drugs          Community resolution   
...                                    ...                           ...   
23437                     Controlled drugs  A no further action disposal   
23438                             Firearms  A no further action disp

## Calling the function get_location for every month of 2019 (every dataframe of the list) and saving it to a csv file

In [28]:
# Adding a new column called "Borough" to the dataframe where the borough will be stored
dfs[0]["Borough"] = dfs[0].apply(get_location, axis=1)

# export the dataframe to a csv file
dfs[0].to_csv('../Data/Police_Data/clean_met_sas_2020/Met_SaS_2020_01.csv', index=False)

1


Hackney
2
Westminster
3
Camden
4
Camden
5
Westminster
6
Camden
7
Westminster
8
Kingston upon Thames
9
10


KeyboardInterrupt: 

In [ ]:
# Adding a new column called "Borough" to the dataframe where the borough will be stored
dfs[1]["Borough"] = dfs[1].apply(get_location, axis=1)

# export the dataframe to a csv file
dfs[1].to_csv('../Data/Police_Data/clean_met_sas_2020/Met_SaS_2020_02.csv', index=False)

211722
Westminster
211723
Croydon
211724
Croydon
211725
Richmond upon Thames
211726
Southwark
211727
Southwark
211728
Lambeth
211729
Croydon
211730
Tower Hamlets
211731
Hillingdon
211732
Richmond upon Thames
211733
Croydon
211734
Croydon
211735
Richmond upon Thames
211736
Croydon
211737
Lambeth
211738
Sutton
211739
Lambeth
211740
Camden
211741
Camden
211742
Islington
211743
Kingston upon Thames
211744
Croydon
211745
Westminster
211746
Kingston upon Thames
211747
Croydon
211748
Newham
211749
Westminster
211750
Southwark
211751
Westminster
211752
Merton
211753
Islington
211754
Merton
211755
Newham
211756
Waltham Forest
211757
Westminster
211758
Sutton
211759
Hackney
211760
Greenwich
211761
Merton
211762
Kingston upon Thames
211763
Lewisham
211764
Lambeth
211765
Camden
211766
Richmond upon Thames
211767
Hammersmith and Fulham
211768
Croydon
211769
Hammersmith and Fulham
211770
Southwark
211771
Croydon
211772
Hammersmith and Fulham
211773
Croydon
211774
Hammersmith and Fulham
211775
Hammer

In [ ]:
# Adding a new column called "Borough" to the dataframe where the borough will be stored
dfs[2]["Borough"] = dfs[2].apply(get_location, axis=1)

# export the dataframe to a csv file
dfs[2].to_csv('../Data/Police_Data/clean_met_sas_2020/Met_SaS_2020_03.csv', index=False)

230091
Waltham Forest
230092
Ealing
230093
Waltham Forest
230094
Bromley
230095
Kingston upon Thames
230096
Waltham Forest
230097
Lewisham
230098
Kingston upon Thames
230099
Bromley
230100
Bexley
230101
Enfield
230102
Camden
230103
Waltham Forest
230104
Ealing
230105
Westminster
230106
Merton
230107
Lambeth
230108
Ealing
230109
Waltham Forest
230110
Hillingdon
230111
Ealing
230112
Waltham Forest
230113
Ealing
230114
Islington
230115
Westminster
230116
Westminster
230117
Waltham Forest
230118
Waltham Forest
230119
Westminster
230120
Westminster
230121
Waltham Forest
230122
Ealing
230123
Westminster
230124
Croydon
230125
Camden
230126
Camden
230127
Ealing
230128
Southwark
230129
Redbridge
230130
Islington
230131
Southwark
230132
Islington
230133
Newham
230134
Sutton
230135
Sutton
230136
Hackney
230137
Bromley
230138
Bromley
230139
Lambeth
230140
Kensington and Chelsea
230141
Sutton
230142
Hounslow
230143
Waltham Forest
230144
Westminster
230145
Waltham Forest
230146
Waltham Forest
230147

In [ ]:
# Adding a new column called "Borough" to the dataframe where the borough will be stored
dfs[3]["Borough"] = dfs[3].apply(get_location, axis=1)

# export the dataframe to a csv file
dfs[3].to_csv('../Data/Police_Data/clean_met_sas_2020/Met_SaS_2020_04.csv', index=False)

248717
Bromley
248718
Hillingdon
248719
Barnet
248720
Tower Hamlets
248721
Tower Hamlets
248722
Tower Hamlets
248723
Havering
248724
Kensington and Chelsea
248725
Newham
248726
Newham
248727
Lambeth
248728
Kingston upon Thames
248729
Newham
248730
Ealing
248731
Hillingdon
248732
Westminster
248733
Westminster
248734
Islington
248735
Lambeth
248736
Lambeth
248737
Tower Hamlets
248738
248739
Camden
248740
Bromley
248741
Camden
248742
Camden
248743
Camden
248744
Ealing
248745
Westminster
248746
Westminster
248747
Bexley
248748
Bexley
248749
Wandsworth
248750
Havering
248751
Wandsworth
248752
Lambeth
248753
Westminster
248754
Camden
248755
Hackney
248756
Camden
248757
Westminster
248758
Brent
248759
Hounslow
248760
Islington
248761
Islington
248762
Islington
248763
Westminster
248764
Southwark
248765
Hillingdon
248766
Hillingdon
248767
Hounslow
248768
Croydon
248769
Croydon
248770
Enfield
248771
Ealing
248772
Brent
248773
Islington
248774
Haringey
248775
Hammersmith and Fulham
248776
Redbr

In [ ]:
# Adding a new column called "Borough" to the dataframe where the borough will be stored
dfs[4]["Borough"] = dfs[4].apply(get_location, axis=1)

# export the dataframe to a csv file
dfs[4].to_csv('../Data/Police_Data/clean_met_sas_2020/Met_SaS_2020_05.csv', index=False)

273638
Islington
273639
Sutton
273640
Lambeth
273641
Kingston upon Thames
273642
Hackney
273643
Camden
273644
Newham
273645
Waltham Forest
273646
Waltham Forest
273647
Waltham Forest
273648
Barking and Dagenham
273649
Hounslow
273650
Lewisham
273651
Westminster
273652
Hounslow
273653
Westminster
273654
Islington
273655
Greenwich
273656
Westminster
273657
Westminster
273658
Waltham Forest
273659
Wandsworth
273660
Westminster
273661
Westminster
273662
Westminster
273663
Westminster
273664
Haringey
273665
Hounslow
273666
Ealing
273667
Hillingdon
273668
Southwark
273669
Ealing
273670
Sutton
273671
Ealing
273672
Bromley
273673
Hillingdon
273674
Ealing
273675
Haringey
273676
Waltham Forest
273677
Newham
273678
Newham
273679
Hounslow
273680
Hammersmith and Fulham
273681
Hammersmith and Fulham
273682
Brent
273683
Hammersmith and Fulham
273684
Brent
273685
Hounslow
273686
Lambeth
273687
Kensington and Chelsea
273688
Kingston upon Thames
273689
Westminster
273690
Kensington and Chelsea
273691
Le

In [ ]:
# Adding a new column called "Borough" to the dataframe where the borough will be stored
dfs[5]["Borough"] = dfs[5].apply(get_location, axis=1)

# export the dataframe to a csv file
dfs[5].to_csv('../Data/Police_Data/clean_met_sas_2020/Met_SaS_2020_06.csv', index=False)

308006
Camden
308007
Waltham Forest
308008
Waltham Forest
308009
Bromley
308010
Enfield
308011
Hounslow
308012
Redbridge
308013
Croydon
308014
Croydon
308015
Croydon
308016
Kingston upon Thames
308017
Kingston upon Thames
308018
Bromley
308019
Newham
308020
Bromley
308021
Westminster
308022
Richmond upon Thames
308023
Westminster
308024
Southwark
308025
Enfield
308026
Hounslow
308027
Hounslow
308028
Westminster
308029
Enfield
308030
Hounslow
308031
Barking and Dagenham
308032
Bromley
308033
Bromley
308034
Bromley
308035
Hounslow
308036
Croydon
308037
Lewisham
308038
Kensington and Chelsea
308039
Newham
308040
Newham
308041
Camden
308042
Hounslow
308043
Kensington and Chelsea
308044
Hounslow
308045
Hounslow
308046
Enfield
308047
Brent
308048
Camden
308049
Bromley
308050
Islington
308051
Camden
308052
Kensington and Chelsea
308053
Islington
308054
Richmond upon Thames
308055
Islington
308056
Kensington and Chelsea
308057
Greenwich
308058
Greenwich
308059
Greenwich
308060
Wandsworth
30806

In [ ]:
# Adding a new column called "Borough" to the dataframe where the borough will be stored
dfs[6]["Borough"] = dfs[6].apply(get_location, axis=1)

# export the dataframe to a csv file
dfs[6].to_csv('../Data/Police_Data/clean_met_sas_2020/Met_SaS_2020_07.csv', index=False)

331079
Wandsworth
331080
Westminster
331081
Westminster
331082
Lambeth
331083
Southwark
331084
Enfield
331085
Sutton
331086
Sutton
331087
Sutton
331088
Sutton
331089
Kensington and Chelsea
331090
Haringey
331091
Sutton
331092
Waltham Forest
331093
Lambeth
331094
Lambeth
331095
Newham
331096
Enfield
331097
Newham
331098
Newham
331099
Lewisham
331100
Lewisham
331101
Lewisham
331102
Westminster
331103
Westminster
331104
Lewisham
331105
Lewisham
331106
Lewisham
331107
Waltham Forest
331108
Redbridge
331109
Waltham Forest
331110
Hounslow
331111
Newham
331112
Waltham Forest
331113
Lambeth
331114
Waltham Forest
331115
Lambeth
331116
Greenwich
331117
Redbridge
331118
Lewisham
331119
Lambeth
331120
Greenwich
331121
Hounslow
331122
Westminster
331123
Kensington and Chelsea
331124
Southwark
331125
Southwark
331126
Southwark
331127
Southwark
331128
Lewisham
331129
Newham
331130
Newham
331131
Bromley
331132
Tower Hamlets
331133
Southwark
331134
Bromley
331135
Tower Hamlets
331136
Bromley
331137
Gre

In [ ]:
# Adding a new column called "Borough" to the dataframe where the borough will be stored
dfs[7]["Borough"] = dfs[7].apply(get_location, axis=1)

# export the dataframe to a csv file
dfs[7].to_csv('../Data/Police_Data/clean_met_sas_2020/Met_SaS_2020_08.csv', index=False)

350907
Richmond upon Thames
350908
Waltham Forest
350909
Richmond upon Thames
350910
350911
Barking and Dagenham
350912
Southwark
350913
Westminster
350914
Croydon
350915
Barking and Dagenham
350916
Croydon
350917
Westminster
350918
Wandsworth
350919
Barking and Dagenham
350920
Kensington and Chelsea
350921
Merton
350922
Redbridge
350923
Redbridge
350924
Redbridge
350925
Waltham Forest
350926
Barnet
350927
Barking and Dagenham
350928
Lambeth
350929
Hackney
350930
Bromley
350931
Merton
350932
Croydon
350933
Westminster
350934
Southwark
350935
Hounslow
350936
Hounslow
350937
Tower Hamlets
350938
Greenwich
350939
Hackney
350940
Greenwich
350941
Tower Hamlets
350942
Merton
350943
Camden
350944
Wandsworth
350945
Lewisham
350946
Kensington and Chelsea
350947
Lewisham
350948
Hackney
350949
Lambeth
350950
Barnet
350951
Lambeth
350952
Lambeth
350953
Lambeth
350954
Kensington and Chelsea
350955
Westminster
350956
Westminster
350957
Hackney
350958
Southwark
350959
Hillingdon
350960
Ealing
350961


In [ ]:
# Adding a new column called "Borough" to the dataframe where the borough will be stored
dfs[8]["Borough"] = dfs[8].apply(get_location, axis=1)

# export the dataframe to a csv file
dfs[8].to_csv('../Data/Police_Data/clean_met_sas_2020/Met_SaS_2020_09.csv', index=False)

366295
Havering
366296
Sutton
366297
Newham
366298
Greenwich
366299
Croydon
366300
Southwark
366301
366302
Newham
366303
Newham
366304
Greenwich
366305
Southwark
366306
Havering
366307
Barnet
366308
Barnet
366309
Barnet
366310
Croydon
366311
Croydon
366312
Lambeth
366313
Newham
366314
Harrow
366315
Lambeth
366316
Southwark
366317
Greenwich
366318
Lambeth
366319
Lambeth
366320
Tower Hamlets
366321
Kingston upon Thames
366322
Newham
366323
Kingston upon Thames
366324
Lambeth
366325
Newham
366326
Tower Hamlets
366327
Westminster
366328
Newham
366329
Newham
366330
Lewisham
366331
Lewisham
366332
Waltham Forest
366333
Waltham Forest
366334
Waltham Forest
366335
Newham
366336
Kingston upon Thames
366337
Waltham Forest
366338
Westminster
366339
Newham
366340
Newham
366341
Richmond upon Thames
366342
Westminster
366343
Redbridge
366344
Waltham Forest
366345
Westminster
366346
Redbridge
366347
Camden
366348
Tower Hamlets
366349
Newham
366350
Hillingdon
366351
Waltham Forest
366352
Waltham Fores

In [ ]:
# Adding a new column called "Borough" to the dataframe where the borough will be stored
dfs[9]["Borough"] = dfs[9].apply(get_location, axis=1)

# export the dataframe to a csv file
dfs[9].to_csv('../Data/Police_Data/clean_met_sas_2020/Met_SaS_2020_10.csv', index=False)

381488
Kingston upon Thames
381489
Southwark
381490
Westminster
381491
Newham
381492
Croydon
381493
Barnet
381494
Barnet
381495
Camden
381496
Southwark
381497
Havering
381498
Southwark
381499
Waltham Forest
381500
Tower Hamlets
381501
Bromley
381502
Southwark
381503
Hillingdon
381504
Bromley
381505
Bromley
381506
Hillingdon
381507
Croydon
381508
Barnet
381509
Hillingdon
381510
Richmond upon Thames
381511
Greenwich
381512
Richmond upon Thames
381513
Tower Hamlets
381514
Tower Hamlets
381515
Tower Hamlets
381516
Greenwich
381517
Greenwich
381518
Richmond upon Thames
381519
Camden
381520
Tower Hamlets
381521
Bromley
381522
Hackney
381523
Hackney
381524
Bexley
381525
Hackney
381526
Hackney
381527
Hackney
381528
Barnet
381529
Lambeth
381530
Havering
381531
Islington
381532
Tower Hamlets
381533
Lambeth
381534
Tower Hamlets
381535
Tower Hamlets
381536
Hounslow
381537
Brent
381538
Bromley
381539
Lewisham
381540
Lambeth
381541
Southwark
381542
Westminster
381543
Hounslow
381544
Westminster
3815

In [ ]:
# Adding a new column called "Borough" to the dataframe where the borough will be stored
dfs[10]["Borough"] = dfs[10].apply(get_location, axis=1)

# export the dataframe to a csv file
dfs[10].to_csv('../Data/Police_Data/clean_met_sas_2020/Met_SaS_2020_11.csv', index=False)

400374
Southwark
400375
Redbridge
400376
Haringey
400377
Ealing
400378
Tower Hamlets
400379
Lewisham
400380
Wandsworth
400381
Bexley
400382
Enfield
400383
Westminster
400384
Southwark
400385
Waltham Forest
400386
Newham
400387
Bromley
400388
Brent
400389
Ealing
400390
Greenwich
400391
Haringey
400392
Haringey
400393
Haringey
400394
Bromley
400395
Ealing
400396
Brent
400397
Brent
400398
Newham
400399
Haringey
400400
Haringey
400401
Enfield
400402
Haringey
400403
Southwark
400404
Southwark
400405
Ealing
400406
Croydon
400407
Southwark
400408
Southwark
400409
Enfield
400410
Islington
400411
Newham
400412
Bromley
400413
Kingston upon Thames
400414
Lewisham
400415
Croydon
400416
Croydon
400417
Croydon
400418
Enfield
400419
Kensington and Chelsea
400420
Bromley
400421
Ealing
400422
Enfield
400423
Brent
400424
Haringey
400425
Brent
400426
Lambeth
400427
Lambeth
400428
Brent
400429
Brent
400430
Brent
400431
Brent
400432
Bromley
400433
Bromley
400434
Ealing
400435
Southwark
400436
Hackney
40043

In [ ]:
# Adding a new column called "Borough" to the dataframe where the borough will be stored
dfs[11]["Borough"] = dfs[11].apply(get_location, axis=1)

# export the dataframe to a csv file
dfs[11].to_csv('../Data/Police_Data/clean_met_sas_2020/Met_SaS_2020_12.csv', index=False)

420755
Tower Hamlets
420756
Richmond upon Thames
420757
Richmond upon Thames
420758
Richmond upon Thames
420759
Wandsworth
420760
Sutton
420761
Richmond upon Thames
420762
Redbridge
420763
Redbridge
420764
Hounslow
420765
Croydon
420766
Lambeth
420767
Westminster
420768
Wandsworth
420769
Redbridge
420770
Lambeth
420771
Redbridge
420772
Barnet
420773
Kensington and Chelsea
420774
Westminster
420775
Westminster
420776
Camden
420777
Camden
420778
Kingston upon Thames
420779
Kensington and Chelsea
420780
Lambeth
420781
Lambeth
420782
Bromley
420783
Redbridge
420784
Bromley
420785
Redbridge
420786
Wandsworth
420787
Redbridge
420788
Wandsworth
420789
Tower Hamlets
420790
Sutton
420791
Bromley
420792
Bromley
420793
Wandsworth
420794
Lambeth
420795
Lambeth
420796
Southwark
420797
Enfield
420798
Ealing
420799
Merton
420800
Richmond upon Thames
420801
Enfield
420802
Croydon
420803
Wandsworth
420804
Richmond upon Thames
420805
Croydon
420806
Wandsworth
420807
Greenwich
420808
Waltham Forest
42080